## 10-fold Cross Validation on the Stanik dataset

In [ ]:
# Imports
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
!pip install simpletransformers
from simpletransformers.classification import ClassificationModel, ClassificationArgs
from sklearn.model_selection import KFold
from sklearn.metrics import accuracy_score
from sklearn.metrics import precision_recall_fscore_support
from sklearn.metrics import f1_score, recall_score, precision_score
from sklearn.metrics import matthews_corrcoef

# Check GPU
gpu_info = !nvidia-smi
gpu_info = '\n'.join(gpu_info)
if gpu_info.find('failed') >= 0:
  print('Not connected to a GPU')
else:
  print(gpu_info)

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     |████████████████████████████████| 250 kB 4.7 MB/s 
     |████████████████████████████████| 43 kB 2.5 MB/s 
     |████████████████████████████████| 1.9 MB 62.1 MB/s 
     |████████████████████████████████| 10.3 MB 53.9 MB/s 
     |████████████████████████████████| 5.5 MB 74.0 MB/s 
     |████████████████████████████████| 7.6 MB 69.1 MB/s 
     |████████████████████████████████| 451 kB 89.8 MB/s 
     |████████████████████████████████| 1.3 MB 73.7 MB/s 
     |████████████████████████████████| 182 kB 82.0 MB/s 
     |████████████████████████████████| 182 kB 87.4 MB/s 
     |████████████████████████████████| 168 kB 74.4 MB/s 
     |████████████████████████████████| 63 kB 2.0 MB/s 
     |████████████████████████████████| 168 kB 82.4 MB/s 
     |████████████████████████████████| 166 kB 83.3 MB/s 
     |████████████████████████████████| 166 kB 81.1 MB/s 
     |█████████████████████████████

In [ ]:
# Import downsampled dataset
df = pd.read_excel('DATASET_downsampled_test3.xlsx')

df = df.drop(columns = ['Unnamed: 0'])

df.info()

Mounted at /content/drive
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2592 entries, 0 to 2591
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       2592 non-null   object
 1   kano_labels  2592 non-null   object
 2   labels       2592 non-null   int64 
dtypes: int64(1), object(2)
memory usage: 60.9+ KB


In [ ]:
# Show the distribution of the labels
print(df['labels'].value_counts())

1    648
3    648
2    648
0    648
Name: labels, dtype: int64


In [ ]:
# Rename the columns so that simple transformers can handle them
train_data = df[['review','labels']]
train_data.columns = ['text', 'labels']
train_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2592 entries, 0 to 2591
Data columns (total 2 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   text    2592 non-null   object
 1   labels  2592 non-null   int64 
dtypes: int64(1), object(1)
memory usage: 40.6+ KB


In [ ]:
# Model implementation and k-fold cross validation with Simpletransformers

# Wrapper function to calculate f1-score with additional parameters
def f1_multiclass(labels, preds):
    return f1_score(labels, preds, average = None)

# Wrapper function to calculate recall with additional parameters
def recall_multiclass(labels, preds):
    return recall_score(labels, preds, average = None)

# Wrapper function to calculate precision with additional parameters
def precision_multiclass(labels, preds):
    return precision_score(labels, preds, average = None)

# K-fold cross validation with 10 folds
n = 10
kf = KFold(n_splits=n, random_state = 42, shuffle = True)

# Lists to store the values of accuracy, f1-score, precision and recall for all 10 folds
resultsAcc = []
resultsf1 = []
resultsPrecision = []
resultsRecall = []

model_args = ClassificationArgs(
    num_train_epochs=1, 
    use_multiprocessing=False,
    use_multiprocessing_for_evaluation=False,
    overwrite_output_dir= True
)

# Create the ClassificationModel
model = ClassificationModel(
    'bert',
    'bert-base-cased',
    num_labels=4,
    args=model_args,
    #use_cuda=False
) 

for train_index, val_index in kf.split(train_data):
  train_df = train_data.iloc[train_index]
  val_df = train_data.iloc[val_index]

  model.train_model(train_df)
  result, model_outputs, wrong_predictions = model.eval_model(val_df, f1=f1_multiclass, acc=accuracy_score, recall=recall_multiclass, precision=precision_multiclass)
  print(result)
  
  # Add scores to the respective lists
  resultsAcc.append(result['acc'])
  resultsf1.append(result['f1'])
  resultsPrecision.append(result['precision'])
  resultsRecall.append(result['recall'])

  print("results accuracy",resultsAcc)
  print(f"Mean-Precision: {sum(resultsAcc) / len(resultsAcc)}")
  print('results f1: ', resultsf1)
  print('results precision: ', resultsPrecision)
  print('results recall: ', resultsRecall)

Downloading:   0%|          | 0.00/570 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/436M [00:00<?, ?B/s]

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForSequenceClassification: ['cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at b

Downloading:   0%|          | 0.00/29.0 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/213k [00:00<?, ?B/s]

...

{'mcc': 0.9845509913454242, 'f1': array([0.99186992, 0.97674419, 0.99145299, 0.99328859]), 'acc': 0.9884169884169884, 'recall': array([0.98387097, 0.96923077, 1.        , 1.        ]), 'precision': array([1.        , 0.984375  , 0.98305085, 0.98666667]), 'eval_loss': 0.0372302350076621}
results accuracy [0.7192307692307692, 0.85, 0.9073359073359073, 0.9227799227799228, 0.9343629343629344, 0.9806949806949807, 0.9884169884169884, 0.9845559845559846, 0.9884169884169884]
Mean-Precision: 0.9195327195327196
results f1:  [array([0.81751825, 0.67716535, 0.83916084, 0.49557522]), array([0.93129771, 0.83443709, 0.82568807, 0.80620155]), array([0.95081967, 0.8627451 , 0.93706294, 0.87417219]), array([0.98571429, 0.875     , 0.96969697, 0.84313725]), array([0.97101449, 0.91472868, 0.96      , 0.90066225]), array([0.97902098, 0.99212598, 0.99130435, 0.96240602]), array([1.        , 0.97520661, 0.99224806, 0.98333333]), array([0.97959184, 0.99259259, 0.98666667, 0.97777778]), array([0.99186992, 0.97

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/292 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/33 [00:00<?, ?it/s]

{'mcc': 0.9948614950005663, 'f1': array([0.99173554, 1.        , 0.99280576, 1.        ]), 'acc': 0.9961389961389961, 'recall': array([0.98360656, 1.        , 1.        , 1.        ]), 'precision': array([1.        , 1.        , 0.98571429, 1.        ]), 'eval_loss': 0.020414975104909954}
results accuracy [0.7192307692307692, 0.85, 0.9073359073359073, 0.9227799227799228, 0.9343629343629344, 0.9806949806949807, 0.9884169884169884, 0.9845559845559846, 0.9884169884169884, 0.9961389961389961]
Mean-Precision: 0.9271933471933472
results f1:  [array([0.81751825, 0.67716535, 0.83916084, 0.49557522]), array([0.93129771, 0.83443709, 0.82568807, 0.80620155]), array([0.95081967, 0.8627451 , 0.93706294, 0.87417219]), array([0.98571429, 0.875     , 0.96969697, 0.84313725]), array([0.97101449, 0.91472868, 0.96      , 0.90066225]), array([0.97902098, 0.99212598, 0.99130435, 0.96240602]), array([1.        , 0.97520661, 0.99224806, 0.98333333]), array([0.97959184, 0.99259259, 0.98666667, 0.97777778]), a

In [ ]:
print("results accuracy",resultsAcc)
print(f"Mean-accuracy: {sum(resultsAcc) / len(resultsAcc)}")
print('results f1: ', resultsf1)
print('results precision: ', resultsPrecision)
print('results recall: ', resultsRecall)

results accuracy [0.7192307692307692, 0.85, 0.9073359073359073, 0.9227799227799228, 0.9343629343629344, 0.9806949806949807, 0.9884169884169884, 0.9845559845559846, 0.9884169884169884, 0.9961389961389961]
Mean-accuracy: 0.9271933471933472
results f1:  [array([0.81751825, 0.67716535, 0.83916084, 0.49557522]), array([0.93129771, 0.83443709, 0.82568807, 0.80620155]), array([0.95081967, 0.8627451 , 0.93706294, 0.87417219]), array([0.98571429, 0.875     , 0.96969697, 0.84313725]), array([0.97101449, 0.91472868, 0.96      , 0.90066225]), array([0.97902098, 0.99212598, 0.99130435, 0.96240602]), array([1.        , 0.97520661, 0.99224806, 0.98333333]), array([0.97959184, 0.99259259, 0.98666667, 0.97777778]), array([0.99186992, 0.97674419, 0.99145299, 0.99328859]), array([0.99173554, 1.        , 0.99280576, 1.        ])]
results precision:  [array([0.8       , 0.70491803, 0.85714286, 0.47457627]), array([0.89705882, 0.79746835, 0.9       , 0.82539683]), array([0.98305085, 0.8627451 , 0.97101449, 

In [ ]:
# Calculate the average precision, recall and f1-scores of the 10 folds for each label

def PrecisionRecallF1Table(resultsPrecision, resultsRecall, resultsf1):

  np_resultsPrecision = np.array(resultsPrecision)
  np_resultsRecall = np.array(resultsRecall)
  np_resultsf1  = np.array(resultsf1)

  # Calculate the mean precision for each label
  df_resultsPrecision = pd.DataFrame(np_resultsPrecision, columns=list('BDIP'))
  precision_b_mean = df_resultsPrecision['B'].mean()
  precision_d_mean = df_resultsPrecision['D'].mean()
  precision_i_mean = df_resultsPrecision['I'].mean()
  precision_p_mean = df_resultsPrecision['P'].mean()

  # Calculate the mean recall for each label
  df_resultsRecall = pd.DataFrame(np_resultsRecall, columns=list('BDIP'))
  recall_b_mean = df_resultsRecall['B'].mean()
  recall_d_mean = df_resultsRecall['D'].mean()
  recall_i_mean = df_resultsRecall['I'].mean()
  recall_p_mean = df_resultsRecall['P'].mean()

  # Calculate the mean f1-score for each label
  df_resultsf1 = pd.DataFrame(np_resultsf1, columns=list('BDIP'))
  f1_b_mean = df_resultsf1['B'].mean()
  f1_d_mean = df_resultsf1['D'].mean()
  f1_i_mean = df_resultsf1['I'].mean()
  f1_p_mean = df_resultsf1['P'].mean()

  # Create dataframe with summarized results
  metrics = [{'B': precision_b_mean, 'D': precision_d_mean, 'I': precision_i_mean, 'P':precision_p_mean},
          {'B': recall_b_mean, 'D': recall_d_mean, 'I': recall_i_mean, 'P': recall_p_mean},
          {'B': f1_b_mean, 'D': f1_d_mean, 'I': f1_i_mean, 'P': f1_p_mean} ]
  train_df_metrics = pd.DataFrame(metrics, index=['Average precision',
                                'Average recall',
                                'Average F1-Score'])
  return train_df_metrics

PrecisionRecallF1Table(resultsPrecision, resultsRecall, resultsf1)

B         D         I         P
Average precision  0.956947  0.905871  0.963288  0.884071
Average recall     0.963523  0.915755  0.935495  0.885282
Average F1-Score   0.959858  0.910075  0.948609  0.883655

## Testing on the Brunotte dataset

In [ ]:
# Import of 'Trainingskorpus_Final', which gives the final labeling
testset1 = pd.read_excel('Trainingskorpus_Final.xlsx')

testset1 = testset1.drop(columns = ['Unnamed: 0'])
testset1.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1622 entries, 0 to 1621
Data columns (total 2 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       1622 non-null   object
 1   kano_labels  1622 non-null   object
dtypes: object(2)
memory usage: 25.5+ KB


In [ ]:
# Show the distribution of the labels
print(testset1['kano_labels'].value_counts())

B    1102
P     395
D      95
I      30
Name: kano_labels, dtype: int64


In [ ]:
# Import of 'Trainingskorpus_InitialLabels', which gives the initial labeling of two sometimes differing labels
testset2 = pd.read_excel('Trainingskorpus_InitialLabels.xlsx')

testset2 = testset2.drop(columns = ['Unnamed: 0'])
testset2.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1622 entries, 0 to 1621
Data columns (total 3 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   review   1622 non-null   object
 1   label 1  1622 non-null   object
 2   label 2  1622 non-null   object
dtypes: object(3)
memory usage: 38.1+ KB


In [ ]:
# Merge the two sets so we have the final labels as well as the initial labels in the testset
testset = testset1.merge(testset2, left_on='review', right_on='review')
testset.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1622 entries, 0 to 1621
Data columns (total 4 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review       1622 non-null   object
 1   kano_labels  1622 non-null   object
 2   label 1      1622 non-null   object
 3   label 2      1622 non-null   object
dtypes: object(4)
memory usage: 63.4+ KB


In [ ]:
# Add a column 'equal' which is True if the two initial labels are equal and false otherwise
equal = [None]*np.size(testset['review'])

# Add a column 'equal01' which stores binary values (1 if the two initial labels are equal, 0 otherwise) to calculate the phi-coefficient
equal01 = [None]*np.size(testset['review'])

# Add a column 'labeled_correctly01' which stores binary values (1 if the model correctly labeled the text, 0 otherwise) to calculate the phi-coefficient
labeled_correctly01 = [None]*np.size(testset['review'])

# Add a column 'prediction' which contains the model's predictions
prediction = [None]*np.size(testset['review'])

i = 0
for label1, label2 in zip(testset['label 1'], testset['label 2']):
  if(label1 == label2):
    equal[i] = True
    equal01[i] = 1
  else:
    equal[i] = False
    equal01[i] = 0
  i += 1
  
testset['equal'] = equal

In [ ]:
# Calculate the accuracy of the whole testset as well as 
# only the parts where the inital two labels are equal (accuracy_clear)
# or differ (accuracy_diff)

accuracy_clear = 0.
accuracy_diff = 0.
n_clear = 0
n_diff = 0
all_predicted_labels = []
predicted_labels_equal_initial_label = []
predicted_labels_diff_initial_label = []
true_label_equal = []
true_label_diff = []

# counter to go through all the reviews and fill the column 'labeled_correctly' with true if they have been labeled correctly, and false if not
i = 0

for label, review, equal in zip(testset['kano_labels'],  testset['review'], testset['equal']):
  
  test_prediction, raw_outputs = model.predict([review])
  
  predicted_label = ''

  if test_prediction[0] == 0:
    predicted_label = 'B'
    prediction[i] = 'B'
  if test_prediction[0] == 1:
    predicted_label = 'D'
    prediction[i] = 'D'
  if test_prediction[0] == 2:
    predicted_label = 'I'
    prediction[i] = 'I'
  if test_prediction[0] == 3:
    predicted_label = 'P'
    prediction[i] = 'P'

  all_predicted_labels.append(predicted_label)
  
  if equal:
    n_clear += 1
    predicted_labels_equal_initial_label.append(predicted_label)
    true_label_equal.append(label)
    if label == predicted_label:
      accuracy_clear += 1.

  if not equal:
    n_diff += 1
    predicted_labels_diff_initial_label.append(predicted_label)
    true_label_diff.append(label)
    if label == predicted_label:
      accuracy_diff += 1.

  if label == predicted_label:
    labeled_correctly01[i] = 1
  else:
    labeled_correctly01[i] = 0
  i+=1

testset['labeled_correctly'] = labeled_correctly01
testset['prediction'] = prediction

accuracy = (accuracy_clear + accuracy_diff) / (n_clear + n_diff)

accuracy_clear /= n_clear
accuracy_diff /= n_diff

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
testset.to_excel("Brunotte_with_predictions_test3_bert.xlsx")  

In [ ]:
print('Accuracy Trainingskorpus:                                                  ', round(accuracy*100, 2), '%,  n =', (n_clear + n_diff))
print('Accuracy Trainingskorpus only on the data that coincides on initial labels:', round(accuracy_clear*100, 2), '%,  n =', n_clear)
print('Accuracy Trainingskorpus only on the data that differs on initial labels:  ', round(accuracy_diff*100, 2), '%,  n = ', n_diff)

Accuracy Trainingskorpus:                                                   72.13 %,  n = 1622
Accuracy Trainingskorpus only on the data that coincides on initial labels: 77.15 %,  n = 1383
Accuracy Trainingskorpus only on the data that differs on initial labels:   43.1 %,  n =  239


In [ ]:
# Calculate precision, recall and f1-score for each label

test_df_metrics = precision_recall_fscore_support(testset['kano_labels'], all_predicted_labels, average=None,labels=['B', 'D', 'I', 'P'])

print('Precision B: ', test_df_metrics[0][0])
print('Precision D: ', test_df_metrics[0][1])
print('Precision I: ', test_df_metrics[0][2])
print('Precision P: ', test_df_metrics[0][3])

print('Recall B: ', test_df_metrics[1][0])
print('Recall D: ', test_df_metrics[1][1])
print('Recall I: ', test_df_metrics[1][2])
print('Recall P: ', test_df_metrics[1][3])

print('F1-score B: ', test_df_metrics[2][0])
print('F1-score D: ', test_df_metrics[2][1])
print('F1-score I: ', test_df_metrics[2][2])
print('F1-score P: ', test_df_metrics[2][3])

Precision B:  0.8797595190380761
Precision D:  0.36231884057971014
Precision I:  0.25
Precision P:  0.5230024213075061
Recall B:  0.7967332123411979
Recall D:  0.7894736842105263
Recall I:  0.03333333333333333
Recall P:  0.5468354430379747
F1-score B:  0.8361904761904763
F1-score D:  0.49668874172185434
F1-score I:  0.058823529411764705
F1-score P:  0.5346534653465347


In [ ]:
# Calculates the phi-coefficient of the labels being predicted correctly and the researchers being 

print('MCC for initial agreement of raters and correct or false labeling',matthews_corrcoef(labeled_correctly01, equal01))

MCC for initial agreement of raters and correct or false labeling 0.2692324037668484


## 10-fold Cross Validation on a combination of the Stanik dataset and the Brunotte dataset

In [ ]:
# Import combined downsampled dataset 
df_combined = pd.read_excel('DATASET_Trainingskorpus_combined_test3.xlsx')

df_combined = df_combined.drop(columns = ['Unnamed: 0'])

# Rename column so that simple transformers can handle it
df_combined = df_combined.rename(columns = {'review': 'text'})
df_combined.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2972 entries, 0 to 2971
Data columns (total 3 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   text         2972 non-null   object
 1   kano_labels  2972 non-null   object
 2   labels       2972 non-null   int64 
dtypes: int64(1), object(2)
memory usage: 69.8+ KB


In [ ]:
# Show the distribution of the labels
print(df_combined['labels'].value_counts())

1    743
0    743
2    743
3    743
Name: labels, dtype: int64


In [ ]:
# 10-fold cross validation on the combined dataset

n2 = 10
kf2 = KFold(n_splits=n2, random_state = 42, shuffle = True)

# Lists to store the values of accuracy, f1-score, precision and recall for all 10 folds
resultsAcc2 = []
resultsf12 = []
resultsPrecision2 = []
resultsRecall2 = []

model_args2 = ClassificationArgs(
    num_train_epochs=1, 
    use_multiprocessing=False,
    use_multiprocessing_for_evaluation=False,
    overwrite_output_dir= True
)

# Create a ClassificationModel
model2 = ClassificationModel(
    'bert',
    'bert-base-cased',
    num_labels=4,
    args=model_args,
    #use_cuda=False
) 

for train_index, val_index in kf2.split(df_combined):
  train_df2 = df_combined.iloc[train_index]
  val_df2 = df_combined.iloc[val_index]

  model2.train_model(df_combined)
  result2, model_outputs2, wrong_predictions2 = model2.eval_model(val_df2, f1=f1_multiclass, acc=accuracy_score, recall=recall_multiclass, precision=precision_multiclass)

  print(result2)
  # Add scores to the respective lists
  resultsAcc2.append(result2['acc'])
  resultsf12.append(result2['f1'])
  resultsPrecision2.append(result2['precision'])
  resultsRecall2.append(result2['recall'])

  print("results accuracy",resultsAcc2)
  print(f"Mean-accuracy: {sum(resultsAcc2) / len(resultsAcc2)}")
  print('results f1: ', resultsf12)
  print('results precision: ', resultsPrecision2)
  print('results recall: ', resultsRecall2)


Some weights of the model checkpoint at bert-base-cased were not used when initializing BertForSequenceClassification: ['cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at b

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/372 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/38 [00:00<?, ?it/s]

{'mcc': 0.8236487199003981, 'f1': array([0.94267516, 0.82352941, 0.90540541, 0.7826087 ]), 'acc': 0.8657718120805369, 'recall': array([0.97368421, 0.88732394, 0.90540541, 0.7012987 ]), 'precision': array([0.91358025, 0.76829268, 0.90540541, 0.8852459 ]), 'eval_loss': 0.40742959474262436}
results accuracy [0.8657718120805369]
Mean-accuracy: 0.8657718120805369
results f1:  [array([0.94267516, 0.82352941, 0.90540541, 0.7826087 ])]
results precision:  [array([0.91358025, 0.76829268, 0.90540541, 0.8852459 ])]
results recall:  [array([0.97368421, 0.88732394, 0.90540541, 0.7012987 ])]


...

{'mcc': 0.9954869134085477, 'f1': array([0.99319728, 1.        , 1.        , 0.99363057]), 'acc': 0.9966329966329966, 'recall': array([1.        , 1.        , 1.        , 0.98734177]), 'precision': array([0.98648649, 1.        , 1.        , 1.        ]), 'eval_loss': 0.013255799287243894}
results accuracy [0.8657718120805369, 0.9026845637583892, 0.9528619528619529, 0.9562289562289562, 0.9764309764309764, 0.9966329966329966, 0.9932659932659933, 0.98989898989899, 0.9966329966329966]
Mean-accuracy: 0.9589343597546431
results f1:  [array([0.94267516, 0.82352941, 0.90540541, 0.7826087 ]), array([0.97468354, 0.87573964, 0.94285714, 0.80620155]), array([0.98342541, 0.9137931 , 0.99328859, 0.90540541]), array([0.97560976, 0.94814815, 0.9689441 , 0.92537313]), array([1.        , 0.95906433, 1.        , 0.95424837]), array([1.        , 1.        , 0.99441341, 0.99259259]), array([1.        , 0.98611111, 0.99300699, 0.99393939]), array([0.98701299, 0.99346405, 1.        , 0.97841727]), array([0.9

Epoch:   0%|          | 0/1 [00:00<?, ?it/s]

Running Epoch 0 of 1:   0%|          | 0/372 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/38 [00:00<?, ?it/s]

{'mcc': 0.9955203833273089, 'f1': array([1.        , 1.        , 0.99319728, 0.99378882]), 'acc': 0.9966329966329966, 'recall': array([1.        , 1.        , 0.98648649, 1.        ]), 'precision': array([1.        , 1.        , 1.        , 0.98765432]), 'eval_loss': 0.02472558617591858}
results accuracy [0.8657718120805369, 0.9026845637583892, 0.9528619528619529, 0.9562289562289562, 0.9764309764309764, 0.9966329966329966, 0.9932659932659933, 0.98989898989899, 0.9966329966329966, 0.9966329966329966]
Mean-accuracy: 0.9627042234424785
results f1:  [array([0.94267516, 0.82352941, 0.90540541, 0.7826087 ]), array([0.97468354, 0.87573964, 0.94285714, 0.80620155]), array([0.98342541, 0.9137931 , 0.99328859, 0.90540541]), array([0.97560976, 0.94814815, 0.9689441 , 0.92537313]), array([1.        , 0.95906433, 1.        , 0.95424837]), array([1.        , 1.        , 0.99441341, 0.99259259]), array([1.        , 0.98611111, 0.99300699, 0.99393939]), array([0.98701299, 0.99346405, 1.        , 0.978

In [ ]:
print("results accuracy",resultsAcc2)
print(f"Mean-accuracy: {sum(resultsAcc2) / len(resultsAcc2)}")
print('results f1: ', resultsf12)
print('results precision: ', resultsPrecision2)
print('results recall: ', resultsRecall2)

results accuracy [0.8657718120805369, 0.9026845637583892, 0.9528619528619529, 0.9562289562289562, 0.9764309764309764, 0.9966329966329966, 0.9932659932659933, 0.98989898989899, 0.9966329966329966, 0.9966329966329966]
Mean-accuracy: 0.9271933471933472
results f1:  [array([0.94267516, 0.82352941, 0.90540541, 0.7826087 ]), array([0.97468354, 0.87573964, 0.94285714, 0.80620155]), array([0.98342541, 0.9137931 , 0.99328859, 0.90540541]), array([0.97560976, 0.94814815, 0.9689441 , 0.92537313]), array([1.        , 0.95906433, 1.        , 0.95424837]), array([1.        , 1.        , 0.99441341, 0.99259259]), array([1.        , 0.98611111, 0.99300699, 0.99393939]), array([0.98701299, 0.99346405, 1.        , 0.97841727]), array([0.99319728, 1.        , 1.        , 0.99363057]), array([1.        , 1.        , 0.99319728, 0.99378882])]
results precision:  [array([0.91358025, 0.76829268, 0.90540541, 0.8852459 ]), array([0.97468354, 0.83146067, 0.97058824, 0.83870968]), array([0.98888889, 0.9137931 , 

In [ ]:
# Calculate the average precision, recall and f1-scores of the 10 folds for each label

PrecisionRecallF1Table(resultsPrecision2, resultsRecall2, resultsf12)

B         D         I         P
Average precision  0.981361  0.937062  0.982599  0.950562
Average recall     0.990200  0.964461  0.975819  0.917327
Average F1-Score   0.985660  0.949985  0.979111  0.932621